<a href="https://colab.research.google.com/github/Atia6/TraSe-Bangla-RAG/blob/main/TraSe_BanglaRAG.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Perform Google Colab installs (if running in Google Colab)
import os

if "COLAB_GPU" in os.environ:
    print("[INFO] Running in Google Colab, installing requirements.")
    !pip install -U torch==1.13.1 # requires torch 2.1.1+ (for efficient sdpa implementation)
    !#pip install sentence-transformers # for embedding models
    #!pip install accelerate # for quantization model loading
    #!pip install bitsandbytes # for quantizing models (less storage space)
    #!pip install flash-attn --no-build-isolation # for faster attention mechanism = faster LLM inference
    !pip install -q transformers einops accelerate langchain bitsandbytes
    !pip install langchain-community langchain-core
    #!pip install sentencepiece
    !pip install torchvision  # Force reinstall torchvision to ensure you have the latest version.

    #for reranking
    #!pip install rank_bm25




[INFO] Running in Google Colab, installing requirements.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 887.5/887.5 MB 1.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 317.1/317.1 MB 2.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.0/21.0 MB 70.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 849.3/849.3 kB 53.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 557.1/557.1 MB 2.1 MB/s eta 0:00:00
  Attempting uninstall: torch
    Found existing installation: torch 2.3.1+cu121
    Uninstalling torch-2.3.1+cu121:
      Successfully uninstalled torch-2.3.1+cu121
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchaudio 2.3.1+cu121 requires torch==2.3.1, but you have torch 1.13.1 which is incompatible.
torchtext 0.18.0 requires torch>=2.3.0, but you have torch 1.13.1 which is incompatible.
torchvision 0.18.1

In [ ]:
#basic
import numpy as np
import pandas as pd

# for embedding
from transformers import AutoTokenizer, AutoModel, AutoModelForCausalLM
import torch
from sklearn.metrics.pairwise import cosine_similarity
from transformers import BertTokenizer, BertModel

#for LLM
from langchain import HuggingFacePipeline
#from transformers import AutoTokenizer, AutoModelForCausalLM
import transformers
#import torch
from transformers import BitsAndBytesConfig
from langchain import PromptTemplate,  LLMChain

#extras
import random
import re
import ast
from typing import List

# Define helper function to print wrapped text
import textwrap

#google drive
from google.colab import drive
from google.colab import files


In [ ]:
#google drive
from google.colab import drive
from google.colab import files
#from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


### cleaning and embedding

In [ ]:
#my code

#from google.colab import drive
drive.mount('/content/drive')


# Path to your text file
file_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/wiki_00.txt'

# Open and read the file
with open(file_path, 'r') as file:
    content = file.read()

# Print the content
print(content)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
{"url": "https://bn.wikipedia.org/wiki?curid=608", "text": "বাংলা ভাষা\n\nবাংলা ভাষা একটি ইন্দো-আর্য ভাষা, যা দক্ষিণ এশিয়ার বাঙালি জাতির প্রধান কথ্য ও লেখ্য ভাষা। মাতৃভাষীর সংখ্যায় বাংলা ইন্দো-আর্য ভাষা পরিবারের দ্বিতীয়, ইন্দো-ইউরোপীয় ভাষা পরিবারের চতুর্থ ও বিশ্বের ষষ্ঠ বৃহত্তম ভাষা। বাংলা সার্বভৌম জাতিরাষ্ট্র বাংলাদেশের জাতীয় ভাষা ও একমাত্র রাষ্ট্রভাষা এবং ভারতের পশ্চিমবঙ্গ, ত্রিপুরা, আসামের বরাক উপত্যকার সরকারি ভাষা। বঙ্গোপসাগরে অবস্থিত আন্দামান দ্বীপপুঞ্জের প্রধান কথ্য ভাষা বাংলা। এছাড়া ভারতের ঝাড়খণ্ড, বিহার, মেঘালয়, মিজোরাম, উড়িষ্যা রাজ্যগুলোতে উল্লেখযোগ্য পরিমাণে বাংলাভাষী জনগণ রয়েছে। ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা। সারা বিশ্বে সব মিলিয়ে ২৬ কোটির অধিক লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে। বাংলাদেশের জাতীয় সঙ্গীত এবং ভারতের জাতীয় সঙ্গীত ও স্তোত্র বাংলাতে রচিত।\n\nবাংলা ভাষা বিকাশের ইতিহাস ১২০০ বছরের অধিক পুরনো। চর্যাপদ এ ভাষার

In [ ]:
# Correct the string format and clean
corrected_string = content.replace("}\n{", "},{").replace("।", "|").replace("\n\nSection::::", " ").replace("\n\n", " ")

# Print the result
print(corrected_string)

{"url": "https://bn.wikipedia.org/wiki?curid=608", "text": "বাংলা ভাষা\n\nবাংলা ভাষা একটি ইন্দো-আর্য ভাষা, যা দক্ষিণ এশিয়ার বাঙালি জাতির প্রধান কথ্য ও লেখ্য ভাষা| মাতৃভাষীর সংখ্যায় বাংলা ইন্দো-আর্য ভাষা পরিবারের দ্বিতীয়, ইন্দো-ইউরোপীয় ভাষা পরিবারের চতুর্থ ও বিশ্বের ষষ্ঠ বৃহত্তম ভাষা| বাংলা সার্বভৌম জাতিরাষ্ট্র বাংলাদেশের জাতীয় ভাষা ও একমাত্র রাষ্ট্রভাষা এবং ভারতের পশ্চিমবঙ্গ, ত্রিপুরা, আসামের বরাক উপত্যকার সরকারি ভাষা| বঙ্গোপসাগরে অবস্থিত আন্দামান দ্বীপপুঞ্জের প্রধান কথ্য ভাষা বাংলা| এছাড়া ভারতের ঝাড়খণ্ড, বিহার, মেঘালয়, মিজোরাম, উড়িষ্যা রাজ্যগুলোতে উল্লেখযোগ্য পরিমাণে বাংলাভাষী জনগণ রয়েছে| ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা| সারা বিশ্বে সব মিলিয়ে ২৬ কোটির অধিক লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে| বাংলাদেশের জাতীয় সঙ্গীত এবং ভারতের জাতীয় সঙ্গীত ও স্তোত্র বাংলাতে রচিত|\n\nবাংলা ভাষা বিকাশের ইতিহাস ১২০০ বছরের অধিক পুরনো| চর্যাপদ এ ভাষার আদি নিদর্শন| অষ্টম শতক থেকে বাংলায় রচিত সাহিত্যের বিশাল ভাণ্ডারের মধ্য দিয়ে অষ্টাদশ শতকের শেষে এসে বাংলা ভাষা তার বর্তমান রূপ 

In [ ]:
#my code
#import ast

# Function to convert corrected string to a list of dictionaries
def string_to_dict_list(s):
    # Remove the outer brackets
    s = s[1:-1]
    # Split into individual dictionary strings
    dict_strings = s.split("},{")

    # Fix the individual dictionary strings
    dict_strings = [ds if ds.endswith("}") else ds + "}" for ds in dict_strings]
    dict_strings = [ds if ds.startswith("{") else "{" + ds for ds in dict_strings]

    # Convert to list of dictionaries
    dict_list = [ast.literal_eval(ds) for ds in dict_strings]
    return dict_list


# Convert to list of dictionaries
data = string_to_dict_list(corrected_string)



print('data:')
print(data)
print(type(data))

data:
[{'url': 'https://bn.wikipedia.org/wiki?curid=608', 'text': 'বাংলা ভাষা\n\nবাংলা ভাষা একটি ইন্দো-আর্য ভাষা, যা দক্ষিণ এশিয়ার বাঙালি জাতির প্রধান কথ্য ও লেখ্য ভাষা| মাতৃভাষীর সংখ্যায় বাংলা ইন্দো-আর্য ভাষা পরিবারের দ্বিতীয়, ইন্দো-ইউরোপীয় ভাষা পরিবারের চতুর্থ ও বিশ্বের ষষ্ঠ বৃহত্তম ভাষা| বাংলা সার্বভৌম জাতিরাষ্ট্র বাংলাদেশের জাতীয় ভাষা ও একমাত্র রাষ্ট্রভাষা এবং ভারতের পশ্চিমবঙ্গ, ত্রিপুরা, আসামের বরাক উপত্যকার সরকারি ভাষা| বঙ্গোপসাগরে অবস্থিত আন্দামান দ্বীপপুঞ্জের প্রধান কথ্য ভাষা বাংলা| এছাড়া ভারতের ঝাড়খণ্ড, বিহার, মেঘালয়, মিজোরাম, উড়িষ্যা রাজ্যগুলোতে উল্লেখযোগ্য পরিমাণে বাংলাভাষী জনগণ রয়েছে| ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা| সারা বিশ্বে সব মিলিয়ে ২৬ কোটির অধিক লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে| বাংলাদেশের জাতীয় সঙ্গীত এবং ভারতের জাতীয় সঙ্গীত ও স্তোত্র বাংলাতে রচিত|\n\nবাংলা ভাষা বিকাশের ইতিহাস ১২০০ বছরের অধিক পুরনো| চর্যাপদ এ ভাষার আদি নিদর্শন| অষ্টম শতক থেকে বাংলায় রচিত সাহিত্যের বিশাল ভাণ্ডারের মধ্য দিয়ে অষ্টাদশ শতকের শেষে এসে বাংলা ভাষা তার বর্তম

In [ ]:
#import re

def clean_text(text):
    text = re.sub(r'\n+', ' ', text)



    # Replace multiple newlines with a single space
    text = re.sub(r'\n+', ' ', text)

    # Remove 'Section::::'
    text = re.sub(r'section::::', '', text, flags=re.IGNORECASE)

    # Remove special unicode character \u200c (Zero Width Non-Joiner)
    text = text.replace('\u200c', '')

    # Remove quotes
    text = text.replace('"', '').replace("'", '')

    # Remove extra spaces
    text = re.sub(r'\s+', ' ', text).strip()

    # Remove HTML tags
    text = re.sub(r'<.*?>', '', text)

    return text

for item in data:
    item['text'] = clean_text(item['text'])

In [ ]:
for item in data:
    item['id_char_count'] = len(item['text'])
    item['id_word_count'] = len(item['text'].split(" "))
    item['id_sentence_count'] = len(item['text'].split("| "))
    item['id_token_count'] = len(item['text']) / 4
print(data)

[{'url': 'https://bn.wikipedia.org/wiki?curid=608', 'text': 'বাংলা ভাষা বাংলা ভাষা একটি ইন্দো-আর্য ভাষা, যা দক্ষিণ এশিয়ার বাঙালি জাতির প্রধান কথ্য ও লেখ্য ভাষা| মাতৃভাষীর সংখ্যায় বাংলা ইন্দো-আর্য ভাষা পরিবারের দ্বিতীয়, ইন্দো-ইউরোপীয় ভাষা পরিবারের চতুর্থ ও বিশ্বের ষষ্ঠ বৃহত্তম ভাষা| বাংলা সার্বভৌম জাতিরাষ্ট্র বাংলাদেশের জাতীয় ভাষা ও একমাত্র রাষ্ট্রভাষা এবং ভারতের পশ্চিমবঙ্গ, ত্রিপুরা, আসামের বরাক উপত্যকার সরকারি ভাষা| বঙ্গোপসাগরে অবস্থিত আন্দামান দ্বীপপুঞ্জের প্রধান কথ্য ভাষা বাংলা| এছাড়া ভারতের ঝাড়খণ্ড, বিহার, মেঘালয়, মিজোরাম, উড়িষ্যা রাজ্যগুলোতে উল্লেখযোগ্য পরিমাণে বাংলাভাষী জনগণ রয়েছে| ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা| সারা বিশ্বে সব মিলিয়ে ২৬ কোটির অধিক লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে| বাংলাদেশের জাতীয় সঙ্গীত এবং ভারতের জাতীয় সঙ্গীত ও স্তোত্র বাংলাতে রচিত| বাংলা ভাষা বিকাশের ইতিহাস ১২০০ বছরের অধিক পুরনো| চর্যাপদ এ ভাষার আদি নিদর্শন| অষ্টম শতক থেকে বাংলায় রচিত সাহিত্যের বিশাল ভাণ্ডারের মধ্য দিয়ে অষ্টাদশ শতকের শেষে এসে বাংলা ভাষা তার বর্তমান রূপ পরিগ্

In [ ]:
#import random

random.sample(data, k=1)

[{'url': 'https://bn.wikipedia.org/wiki?curid=1098',
  'text': 'বাংলা সাহিত্য বাংলা ভাষায় রচিত সাহিত্যকর্ম বাংলা সাহিত্য নামে পরিচিত| আনুমানিক খ্রিষ্টীয় সপ্তম শতাব্দীর মাঝামাঝি বাংলা ভাষায় সাহিত্য রচনার সূত্রপাত হয়| খ্রিষ্টীয় দশম থেকে দ্বাদশ শতাব্দীর মধ্যবর্তী সময়ে রচিত বৌদ্ধ দোহা-সংকলন চর্যাপদ বাংলা সাহিত্যের প্রাচীনতম নিদর্শন| আবিষ্কারক হরপ্রসাদ শাস্ত্রী আরও তিনটি গ্রন্থের সঙ্গে চর্যাগানগুলি নিয়ে সম্পাদিত গ্রন্থের নাম দেন হাজার বছরের পুরাণ বাঙ্গালা ভাষায় রচিত বৌদ্ধ গান ও দোহা | মধ্যযুগীয় বাংলা সাহিত্য ছিল কাব্যপ্রধান| হিন্দুধর্ম, ইসলাম ও বাংলার লৌকিক ধর্মবিশ্বাসগুলিকে কেন্দ্র করে গড়ে উঠেছিল এই সময়কার বাংলা সাহিত্য| মঙ্গলকাব্য, বৈষ্ণব পদাবলি, শাক্তপদাবলি, বৈষ্ণব সন্তজীবনী, রামায়ণ, মহাভারত ও ভাগবতের বঙ্গানুবাদ, পীরসাহিত্য, নাথসাহিত্য, বাউল পদাবলি এবং ইসলামি ধর্মসাহিত্য ছিল এই সাহিত্যের মূল বিষয়| বাংলা সাহিত্যে আধুনিকতার সূত্রপাত হয় খ্রিষ্টীয় অষ্টাদশ শতাব্দীতে| ঊনবিংশ শতাব্দীতে বাংলার নবজাগরণের যুগে কলকাতা শহরকে কেন্দ্র করে বাংলা সাহিত্যে এক নতুন যুগের সূচনা হয়| এই সময় 

In [ ]:
#import re
#import pandas as pd

def split_into_sentences(paragraph):
    # This regular expression matches sentence-ending punctuation followed by a space and an uppercase letter.
    sentence_endings = re.compile(r'(?<=[|!?]) +')
    sentences = sentence_endings.split(paragraph)
    return sentences

for item in data:
    item['sentences'] = split_into_sentences(item['text'])

#import random

random.sample(data, k=1)

[{'url': 'https://bn.wikipedia.org/wiki?curid=839',
  'text': 'আনন্দমঠ আনন্দমঠ ঊনবিংশ শতাব্দীর ঔপন্যাসিকবঙ্কিমচন্দ্র চট্টোপাধ্যায় বিরচিত একটি বাংলা উপন্যাস| এর প্রকাশকাল ১৮৪৪ খ্রিস্টাব্দ| ভারতবর্ষের স্বাধীনতা সংগ্রামে এর একটি বিশেষ ভূমিকা আছে| এই উপন্যাসটি ছাপার বিরূদ্ধে ব্রিটিশ সরকার আইন পাশ কৱে, তবে এর হস্তলিখিত গুপ্ত সংস্করণ জনগণের মাঝে ছড়িয়ে পড়ে| উপন্যাসটি মুসলমান-বিরোধী মতধারার জন্য কিছুটা বিতর্কিত| এই উপন্যাসের কাহিনী ১৭৭৩ খ্রিস্টাব্দে সংঘটিত উত্তর বঙ্গের সন্ন্যাসী আন্দোলনের ওপর ভিত্তি করে রচিত| এই উপন্যাসেই বঙ্কিমচন্দ্র বন্দে মাতরম গানটি লেখেন| পরবর্তীতে ভারতীয় স্বদেশপ্রেমীরা বন্দে মাতরম বাক্যটি জাতীয়তাবাদী শ্লোগান হিসাবে গ্রহণ করে|',
  'id': '839',
  'title': 'আনন্দমঠ',
  'id_char_count': 590,
  'id_word_count': 78,
  'id_sentence_count': 8,
  'id_token_count': 147.5,
  'sentences': ['আনন্দমঠ আনন্দমঠ ঊনবিংশ শতাব্দীর ঔপন্যাসিকবঙ্কিমচন্দ্র চট্টোপাধ্যায় বিরচিত একটি বাংলা উপন্যাস|',
   'এর প্রকাশকাল ১৮৪৪ খ্রিস্টাব্দ|',
   'ভারতবর্ষের স্বাধীনতা সংগ্রামে এর একটি বিশেষ ভূমিকা আ

In [ ]:
#import pandas as pd

df = pd.DataFrame(data)
df.head()

url  \
0  https://bn.wikipedia.org/wiki?curid=608   
1  https://bn.wikipedia.org/wiki?curid=796   
2  https://bn.wikipedia.org/wiki?curid=822   
3  https://bn.wikipedia.org/wiki?curid=827   
4  https://bn.wikipedia.org/wiki?curid=830   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [ ]:
df.describe().round(2)

id_char_count  id_word_count  id_sentence_count  id_token_count
count          27.00          27.00              27.00           27.00
mean        14148.22        2046.59             130.52         3537.06
std         17145.61        2475.07             150.98         4286.40
min            11.00           2.00               1.00            2.75
25%          2744.00         397.00              24.50          686.00
50%          5142.00         724.00              51.00         1285.50
75%         23476.00        3334.00             230.50         5869.00
max         57274.00        8634.00             476.00        14318.50

In [ ]:
#from typing import List


# Define split size to turn groups of sentences into chunks
num_sentence_chunk_size = 5

# Create a function that recursively splits a list into desired sizes
def split_list(input_list: list,
               slice_size: int) -> List[List[str]]:
    """
    Splits the input_list into sublists of size slice_size (or as close as possible).

    For example, a list of 17 sentences would be split into two lists of [[10], [7]]
    """
    return [input_list[i:i + slice_size] for i in range(0, len(input_list), slice_size)]

# Loop through pages and texts and split sentences into chunks
for item in data:
    item["sentence_chunks"] = split_list(input_list=item["sentences"],
                                         slice_size=num_sentence_chunk_size)
    item["num_chunks"] = len(item["sentence_chunks"])

In [ ]:
def add_space_between_sentences(text):
    # Define the pattern to find sentence endings (। or |) followed by a Bengali character
    pattern = r'([।|])([\u0980-\u09FF])'
    # Define the replacement pattern to add a space between them
    replacement = r'\1 \2'

    # Perform the substitution
    text = re.sub(pattern, replacement, text)

    return text




In [ ]:
#import re

# Split each chunk into its own item
data_and_chunk = []
for item in data:
    for sentence_chunk in item["sentence_chunks"]:
        chunk_dict = {}
        chunk_dict["id"] = item["id"]
        chunk_dict["title"] = item["title"]

        # Join the sentences together into a paragraph-like structure, aka a chunk (so they are a single string)
        joined_sentence_chunk = "".join(sentence_chunk).replace("  ", " ").strip()
        #joined_sentence_chunk = re.sub(r'\.([A-Z])', r'. \1', joined_sentence_chunk) # ".A" -> ". A" for any full-stop/capital letter combo

        joined_sentence_chunk = add_space_between_sentences(joined_sentence_chunk)
        chunk_dict["sentence_chunk"] = joined_sentence_chunk

        # Get stats about the chunk
        chunk_dict["chunk_char_count"] = len(joined_sentence_chunk)
        chunk_dict["chunk_word_count"] = len([word for word in joined_sentence_chunk.split(" ")])
        chunk_dict["chunk_token_count"] = len(joined_sentence_chunk) / 4 # 1 token = ~4 characters

        data_and_chunk.append(chunk_dict)

# How many chunks do we have?
len(data_and_chunk)

718

In [ ]:
#import random

random.sample(data_and_chunk, k=1)

[{'id': '1100',
  'title': 'চট্টগ্রাম',
  'sentence_chunk': 'আইয়ুব বাচ্চু, কুমার বিশ্বজিৎ, রবি চৌধুরী, নাকিব খান, পার্থ বডুয়া, সন্দিপন, নাসিম আলি খান, মিলা ইসলাম চট্টগ্রামের সন্তান| নৃত্যে চট্টগ্রামের ইতিহাস মনে রখার মত| রুনু বিশ্বাস জাতীয় পর্যায়ে বিখ্যাত নৃত্যগুরু| চট্টগ্রামের বিখ্যাত সাংস্কৃতিক সংগঠন হল দৃষ্টি চট্টগ্রাম, বোধন আবৃত্তি পরিষদ, প্রমা, অঙ্গন চট্টগ্রাম বিশ্ববিদ্যালয়, আলাউদ্দিন ললিতকলা একাডেমি, প্রাপন একাডেমি, উদিচি, আবৃত্তি সমন্বয় পরিষদ, ফু্লকি, রবীন্দ্রসঙ্গীত শিল্পী সংস্থা, রক্তকরবী, আর্য সঙ্গীত, সঙ্গীত পরিষদ| মডেল তারকা নোবেল, মৌটুসি, পূর্ণিমা,শ্রাবস্তীর চট্টগ্রামে জন্ম |',
  'chunk_char_count': 538,
  'chunk_word_count': 70,
  'chunk_token_count': 134.5}]

In [ ]:
df = pd.DataFrame(data_and_chunk)
df.describe().round(2)

chunk_char_count  chunk_word_count  chunk_token_count
count            718.00            718.00             718.00
mean             531.11             76.99             132.78
std              189.04             27.29              47.26
min                7.00              1.00               1.75
25%              414.25             60.00             103.56
50%              509.00             74.00             127.25
75%              621.00             89.00             155.25
max             1999.00            275.00             499.75

In [ ]:
# Define the minimum token length
min_token_length = 30

# Get the rows that match the condition
filtered_df = df[df["chunk_token_count"] <= min_token_length]

# Determine the sample size
sample_size = min(5, len(filtered_df))

# Sample the rows
sampled_rows = filtered_df.sample(sample_size)

# Print the sampled rows
for _, row in sampled_rows.iterrows():
    print(f'Chunk token count: {row["chunk_token_count"]} | Text: {row["sentence_chunk"]}')

Chunk token count: 26.0 | Text: অবশ্য গবেষণায় এও বলা হয় যে, চাঁদের মেরু অঞ্চলের নানা গর্তের তলদেশে বরফ থাকলেও চাঁদের অন্য অঞ্চল শুষ্ক|
Chunk token count: 2.75 | Text: প্রধান পাতা
Chunk token count: 19.5 | Text: যেমন ঢাকার প্রমিত সমাজে কথ্যভাষায় তৎসম শব্দের ব্যবহারে অনীহা লক্ষ্য করা যায়|
Chunk token count: 25.5 | Text: বাংলাদেশের রাজধানী ঢাকা, বাণিজ্যনগরী চট্টগ্রাম ও চা-শিল্পের জন্য বিখ্যাত সিলেটে খেলাগুলো অনুষ্ঠিত হয়|
Chunk token count: 1.75 | Text: রাষ্ট্র


In [ ]:
# Define the minimum token length
max_token_length = 380

# Get the rows that match the condition
filtered_df = df[df["chunk_token_count"] >= max_token_length]

# Determine the sample size
sample_size = min(5, len(filtered_df))

# Sample the rows
sampled_rows = filtered_df.sample(sample_size)

# Print the sampled rows
for _, row in sampled_rows.iterrows():
    print(f'Chunk token count: {row["chunk_token_count"]} | Text: {row["sentence_chunk"]}')

Chunk token count: 426.75 | Text: ইউনিকোড কনসোটিয়াম একটি অলাভজনক সংগঠন যেটি ইউনিকোডের উন্নয়নে কাজ করে যাচ্ছে এই সংগঠনের মূল লক্ষ হচ্ছে সকল ভাষাকে একটি নির্দিষ্ট মানদন্ডে নিয়ে আসা| ইতিহাস. ১৯৮৭ সালে ইউনিকোডের কাজ শুরু করেছিলেন জেরোক্স (Xerox) এর জো বেকার (Joe Becker) এবং অ্যাপল (Apple) এর লি কলিন্স (Lee Collins) ও মার্ক ডেভিস (Mark Davis)| তাঁদের মূল লক্ষ্য ছিল সকল ভাষাকে একটি সার্বজনীন সংকেতায়নের মানদন্ডে নিয়ে আসা| ফলশ্রুতিতে পরবর্তী বছরের আগষ্ট মাসে জো বেকার International/multilingual text character encoding system, tentatively called Unicode. (অনুবাদ : আন্তর্জাতিক/বহুভাষিক বর্ণ সংকেতায়ন ব্যবস্থা) নামে একটি খসড়া প্রস্তবনা তৈরি করেন| এই প্রস্তাবনাটি ছিল একটি ১৬ বিট এর বর্ণ সংকেতায়ন ব্যবস্থা: Unicode is intended to address the need for a workable, reliable world text encoding. Unicode could be roughly described as wide-body ASCII that has been stretched to 16 bits to encompass the characters of all the worlds living languages. In a properly engineered design, 16 bits per charact

In [ ]:
#data_and_chunk_over_min_len = df[df["chunk_token_count"] > min_token_length].to_dict(orient="records")
#data_and_chunk_over_min_len[:2]

[{'id': '608',
  'title': 'বাংলা ভাষা',
  'sentence_chunk': 'বাংলা ভাষা বাংলা ভাষা একটি ইন্দো-আর্য ভাষা, যা দক্ষিণ এশিয়ার বাঙালি জাতির প্রধান কথ্য ও লেখ্য ভাষা| মাতৃভাষীর সংখ্যায় বাংলা ইন্দো-আর্য ভাষা পরিবারের দ্বিতীয়, ইন্দো-ইউরোপীয় ভাষা পরিবারের চতুর্থ ও বিশ্বের ষষ্ঠ বৃহত্তম ভাষা| বাংলা সার্বভৌম জাতিরাষ্ট্র বাংলাদেশের জাতীয় ভাষা ও একমাত্র রাষ্ট্রভাষা এবং ভারতের পশ্চিমবঙ্গ, ত্রিপুরা, আসামের বরাক উপত্যকার সরকারি ভাষা| বঙ্গোপসাগরে অবস্থিত আন্দামান দ্বীপপুঞ্জের প্রধান কথ্য ভাষা বাংলা| এছাড়া ভারতের ঝাড়খণ্ড, বিহার, মেঘালয়, মিজোরাম, উড়িষ্যা রাজ্যগুলোতে উল্লেখযোগ্য পরিমাণে বাংলাভাষী জনগণ রয়েছে|',
  'chunk_char_count': 543,
  'chunk_word_count': 72,
  'chunk_token_count': 135.75},
 {'id': '608',
  'title': 'বাংলা ভাষা',
  'sentence_chunk': 'ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা| সারা বিশ্বে সব মিলিয়ে ২৬ কোটির অধিক লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে| বাংলাদেশের জাতীয় সঙ্গীত এবং ভারতের জাতীয় সঙ্গীত ও স্তোত্র বাংলাতে রচিত| বাংলা ভাষা বিকাশের ইতিহাস ১২০০ বছরের অধিক পুরনো| চ

In [ ]:
# Assuming df is your DataFrame and chunk_token_count is the column to filter
data_filtered = df[(df["chunk_token_count"] > min_token_length) & (df["chunk_token_count"] < max_token_length)].to_dict(orient="records")


In [ ]:
df = pd.DataFrame(data_filtered)
df.describe().round(2)

chunk_char_count  chunk_word_count  chunk_token_count
count            710.00            710.00             710.00
mean             531.38             77.03             132.85
std              171.01             24.70              42.75
min              134.00             19.00              33.50
25%              417.25             60.00             104.31
50%              509.00             74.00             127.25
75%              621.00             89.00             155.25
max             1385.00            195.00             346.25

In [ ]:
df.head()

id       title  \
0  608  বাংলা ভাষা   
1  608  বাংলা ভাষা   
2  608  বাংলা ভাষা   
3  608  বাংলা ভাষা   
4  608  বাংলা ভাষা   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            sentence_chunk  \
0                                                                                                                                                                                                                          বাংলা ভাষা বাংলা ভাষা একটি ইন্দো-আর্য ভাষা, যা দক্ষিণ এশিয়ার বাঙালি জাতির প্রধান কথ্য ও লেখ্য ভাষা| মাতৃভাষীর সংখ্যায় বাংলা ইন্দো-আর্য ভাষা পরিবারের দ্বিতীয়, ইন্দো-ইউরোপীয় ভাষা পরিবারের চতুর্থ ও বিশ্বের ষষ্ঠ বৃহত্তম ভাষা| বাংলা সার্বভৌম জাতিরাষ্ট্র বাংলাদেশের জাতীয় ভাষা ও একমাত্র রাষ্ট্রভাষা এবং ভারতের পশ্চিমবঙ্গ, ত্রিপুরা, আসামের বরাক উপত্যকার সরকারি ভাষা| বঙ্গোপসাগরে অবস্থিত আন্দামান দ্বীপপুঞ্জের প্রধান কথ্য ভাষা বাংলা| এছাড়া ভারতের ঝাড়খণ্ড, বিহার, মেঘালয়, মিজোরাম, উড়িষ্যা রাজ্যগুলোতে উল্লেখযোগ্য পরিমাণে বাংলাভাষী জনগণ রয়েছে|   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা| সারা বিশ্বে সব মিলিয়ে ২৬ কোটির অধিক লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে| বাংলাদেশের জাতীয় সঙ্গীত এবং ভারতের জাতীয় সঙ্গীত ও স্তোত্র বাংলাতে রচিত| বাংলা ভাষা বিকাশের ইতিহাস ১২০০ বছরের অধিক পুরনো| চর্যাপদ এ ভাষার আদি নিদর্শন|   
2                                                                                                                                                                                                অষ্টম শতক থেকে বাংলায় রচিত সাহিত্যের বিশাল ভাণ্ডারের মধ্য দিয়ে অষ্টাদশ শতকের শেষে এসে বাংলা ভাষা তার বর্তমান রূপ পরিগ্রহণ করে| বাংলা ভাষার লিপি হল বাংলা লিপি| বাংলাদেশ ও পশ্চিমবঙ্গে প্রচলিত বাংলা ভাষার মধ্যে শব্দগত ও উচ্চারণগত সামান্য পার্থক্য রয়েছে| বাংলার নবজাগরণে ও বাংলার সাংস্কৃতিক বিবিধতাকে এক সূত্রে গ্রন্থনে বাংলা ভাষা ও সাহিত্য সবচেয়ে গুরুত্বপূর্ণ ভূমিকা রেখেছে, এবং বাঙালি জাতীয়তাবাদ তথা বাংলাদেশ গঠনে সবচেয়ে গুরুত্বপূর্ণ ভূমিকা রেখেছে| ১৯৫১-৫২ খ্রিস্টাব্দে পূর্ব বাংলায় সংগঠিত বাংলা ভাষা আন্দোলন এই ভাষার সাথে বাঙালি অস্তিত্বের যোগসূত্র স্থাপন করেছিল|   
3                                                                            ১৯৫২ খ্রিস্টাব্দের ২১শে ফেব্রুয়ারি, ঢাকা বিশ্ববিদ্যালয়ে প্রতিবাদী ছাত্র ও আন্দোলনকারীরা সংখ্যাগরিষ্ঠের মাতৃভাষা বাংলাকে রাষ্ট্রভাষাকরণের দাবীতে নিজেদের জীবন উৎসর্গ করেন| তাঁদের সংগ্রামের স্বীকৃতি স্বরূপ ১৯৯৯ খ্রিস্টাব্দে ইউনেস্কো ২১শে ফেব্রুয়ারি দিনটিকে আন্তর্জাতিক মাতৃভাষা দিবস হিসেবে ঘোষণা করে| ইতিহাস. খ্রিস্টীয় দশম থেকে দ্বাদশ শতাব্দীর মধ্যবর্তী সময়কালে মাগধী প্রাকৃত ও পালির মতো পূর্ব মধ্য ইন্দো-আর্য ভাষাসমূহ থেকে বাংলা ও অন্যান্য পূর্ব ইন্দো-আর্য ভাষাগুলির উদ্ভব ঘটে| এই অঞ্চলে কথ্য ভাষা প্রথম সহস্রাব্দে মাগধী প্রাকৃত বা অর্ধমাগধী ভাষায় বিবর্তিত হয়| খ্রিস্টীয় দশম শতাব্দীর শুরুতে উত্তর ভারতের অন্যান্য প্রাকৃত ভাষার মতোই মাগধী প্রাকৃত থেকে অপভ্রংশ ভাষাগুলির উদ্ভব ঘটে|   
4  পূর্বী অপভ্রংশ বা অবহট্ঠ নামক পূর্ব উপ

In [ ]:
df.iloc[257]

id                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     1098
title                                                                                                                                                                                                                                                                                                                                                                                                                                                                         বাংলা সাহিত্য
sentence_chunk       তবে সংখ্যাধিক্যের হিসেবে কম| আসলে বৈষ্ণব পদাবলির মধ্যে রাধাকৃষ্ণের প্রণয়লীলা স্তরে স্তরে এমন গভীর ও বিস্তৃতভাবে বর্ণিত হয়েছে যে অনেকের ধারণা বাংলা সাহিত্যে এ আসলে একটি রোমান্টিক প্রণয়কাব্যের নমুনা| বস্তুত পৃথিবীর অন্যান্য মধ্যযুগীয় সাহিত্যের মতনই এও বিশেষভাবে ধর্মাশ্রিত ও বৈষ্ণব ধর্মের তত্ত্ববিশ্বের উপরে প্রতিষ্ঠিত| তবে যে কোন ধর্মের মতনই বৈষ্ণব ধর্মতত্ত্বেরও আনেকগুলি ঘরানা ছিল| এর মধ্যে তাত্বিকভাবে সবচেয়ে প্রভাবশালী ছিল বৃন্দাবনের বৈষ্ণবগোষ্ঠী|
chunk_char_count                                                                                                                                                                                                                                                                                                                                                                                                                                                                        454
chunk_word_count                                                                                                                                                                                                                                                                                                                                                                                                                                                                         62
chunk_token_count                                                                                                                                                                                                                                                                                                                                                                                                                                                                     113.5
Name: 257, dtype: object

### Embeddings of chunks by BanglaBERT


In [ ]:
#from transformers import AutoTokenizer, AutoModel
#import torch
#from sklearn.metrics.pairwise import cosine_similarity
#import numpy as np

# Step 3: Load BanglaBERT model and tokenizer
tokenizer = AutoTokenizer.from_pretrained("sagorsarker/bangla-bert-base")
model = AutoModel.from_pretrained("sagorsarker/bangla-bert-base")

config.json:   0%|          | 0.00/491 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/2.24M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/660M [00:00<?, ?B/s]

In [ ]:
# Step 4: Define a function to encode sentences
def encode_sentences(sentences):
    inputs = tokenizer(sentences, return_tensors='pt', padding=True, truncation=True)
    with torch.no_grad():
        outputs = model(**inputs)
    # Mean pooling to get sentence embeddings
    embeddings = outputs.last_hidden_state.mean(dim=1)
    return embeddings.numpy()


In [ ]:
%%time

# Send the model to the GPU
#embedding_model.to("cuda") # requires a GPU installed, for reference on my local machine, I'm using a NVIDIA RTX 4090
i = 0
# Create embeddings one by one on the GPU
for item in data_filtered:
    item["embedding"] = encode_sentences(item["sentence_chunk"])


Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [ ]:
#save
# Save embeddings to file


#from google.colab import drive
#drive.mount('/content/drive')


# Save the DataFrame to a CSV file
#df.to_csv(file_path, index=False)

text_chunks_and_embeddings_df = pd.DataFrame(data_filtered)
embeddings_df_save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/text_chunks_and_embeddings_df3.csv'
text_chunks_and_embeddings_df.to_csv(embeddings_df_save_path, index=True)


In [ ]:
#download for safety

#from google.colab import files
files.download(embeddings_df_save_path)
#files.download('text_chunks_and_embeddings_df2.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Embedding chunks by bert-based-multilingual-cased

In [ ]:


from transformers import BertTokenizer, BertModel


#Load pre-trained model tokenizer and model
tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased')
model = BertModel.from_pretrained('bert-base-multilingual-cased')

#Function to get sentence embedding
def get_sentence_embedding(sentence):
    tokens = tokenizer(sentence, return_tensors='pt', padding=True, truncation=True)
    with torch.no_grad():
        outputs = model(**tokens)
    #Get the mean pooling of token embeddings to represent the sentence
    sentence_embedding = outputs.last_hidden_state.mean(dim=1)
    return sentence_embedding



tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/625 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/714M [00:00<?, ?B/s]

In [ ]:
%%time

# Send the model to the GPU
#embedding_model.to("cuda") # requires a GPU installed, for reference on my local machine, I'm using a NVIDIA RTX 4090
i = 0
# Create embeddings one by one on the GPU
for item in data_filtered:
    item["embedding"] = get_sentence_embedding(item["sentence_chunk"])

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [ ]:
text_chunks_and_embeddings_df = pd.DataFrame(data_filtered)
embeddings_df_save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/text_chunks_and_embeddings_bert_uncased.csv'
text_chunks_and_embeddings_df.to_csv(embeddings_df_save_path, index=True)

### BanglaBERT embedding data processing

In [ ]:
# Import saved file and view

#drive.mount('/content/drive')

# BanglaBert Embedding
embeddings_df_save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/text_chunks_and_embeddings_df3.csv'
text_chunks_and_embedding_BB = pd.read_csv(embeddings_df_save_path)
text_chunks_and_embedding_BB.head(1)

Unnamed: 0   id       title  \
0           0  608  বাংলা ভাষা   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    sentence_chunk  \
0  বাংলা ভাষা বাংলা ভাষা একটি ইন্দো-আর্য ভাষা, যা দক্ষিণ এশিয়ার বাঙালি জাতির প্রধান কথ্য ও লেখ্য ভাষা| মাতৃভাষীর সংখ্যায় বাংলা ইন্দো-আর্য ভাষা পরিবারের দ্বিতীয়, ইন্দো-ইউরোপীয় ভাষা পরিবারের চতুর্থ ও বিশ্বের ষষ্ঠ বৃহত্তম ভাষা| বাংলা সার্বভৌম জাতিরাষ্ট্র বাংলাদেশের জাতীয় ভাষা ও একমাত্র রাষ্ট্রভাষা এবং ভারতের পশ্চিমবঙ্গ, ত্রিপুরা, আসামের বরাক উপত্যকার সরকারি ভাষা| বঙ্গোপসাগরে অবস্থিত আন্দামান দ্বীপপুঞ্জের প্রধান কথ্য ভাষা বাংলা| এছাড়া ভারতের ঝাড়খণ্ড, বিহার, মেঘালয়, মিজোরাম, উড়িষ্যা রাজ্যগুলোতে উল্লেখযোগ্য পরিমাণে বাংলাভাষী জনগণ রয়েছে|   

   chunk_char_count  chunk_word_count  chunk_token_count  \
0               543                72             135.75   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

In [ ]:

# Rename the unnamed column
text_chunks_and_embedding_BB.rename(columns={'Unnamed: 0': 'index'}, inplace=True)

In [ ]:
text_chunks_and_embedding_BB.describe().round(2)

index       id  chunk_char_count  chunk_word_count  chunk_token_count
count  710.00   710.00            710.00            710.00             710.00
mean   354.50  1025.40            531.38             77.03             132.85
std    205.10   131.14            171.01             24.70              42.75
min      0.00   608.00            134.00             19.00              33.50
25%    177.25   867.00            417.25             60.00             104.31
50%    354.50  1100.00            509.00             74.00             127.25
75%    531.75  1109.00            621.00             89.00             155.25
max    709.00  1117.00           1385.00            195.00             346.25

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"

# Convert embedding column back to np.array (it got converted to string when it got saved to CSV)
text_chunks_and_embedding_BB["embedding"] = text_chunks_and_embedding_BB["embedding"].apply(lambda x: np.fromstring(x.strip("[]"), sep=" "))

# Convert texts and embedding df to list of dicts
title_and_chunks = text_chunks_and_embedding_BB.to_dict(orient="records")

# Convert embeddings to torch tensor and send to device (note: NumPy arrays are float64, torch tensors are float32 by default)
embeddings_BB = torch.tensor(np.array(text_chunks_and_embedding_BB["embedding"].tolist()), dtype=torch.float32).to(device)
embeddings_BB.shape

torch.Size([710, 768])

In [ ]:
text_chunks_and_embedding_BB.head()

index   id       title  \
0      0  608  বাংলা ভাষা   
1      1  608  বাংলা ভাষা   
2      2  608  বাংলা ভাষা   
3      3  608  বাংলা ভাষা   
4      4  608  বাংলা ভাষা   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            sentence_chunk  \
0                                                                                                                                                                                                                          বাংলা ভাষা বাংলা ভাষা একটি ইন্দো-আর্য ভাষা, যা দক্ষিণ এশিয়ার বাঙালি জাতির প্রধান কথ্য ও লেখ্য ভাষা| মাতৃভাষীর সংখ্যায় বাংলা ইন্দো-আর্য ভাষা পরিবারের দ্বিতীয়, ইন্দো-ইউরোপীয় ভাষা পরিবারের চতুর্থ ও বিশ্বের ষষ্ঠ বৃহত্তম ভাষা| বাংলা সার্বভৌম জাতিরাষ্ট্র বাংলাদেশের জাতীয় ভাষা ও একমাত্র রাষ্ট্রভাষা এবং ভারতের পশ্চিমবঙ্গ, ত্রিপুরা, আসামের বরাক উপত্যকার সরকারি ভাষা| বঙ্গোপসাগরে অবস্থিত আন্দামান দ্বীপপুঞ্জের প্রধান কথ্য ভাষা বাংলা| এছাড়া ভারতের ঝাড়খণ্ড, বিহার, মেঘালয়, মিজোরাম, উড়িষ্যা রাজ্যগুলোতে উল্লেখযোগ্য পরিমাণে বাংলাভাষী জনগণ রয়েছে|   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা| সারা বিশ্বে সব মিলিয়ে ২৬ কোটির অধিক লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে| বাংলাদেশের জাতীয় সঙ্গীত এবং ভারতের জাতীয় সঙ্গীত ও স্তোত্র বাংলাতে রচিত| বাংলা ভাষা বিকাশের ইতিহাস ১২০০ বছরের অধিক পুরনো| চর্যাপদ এ ভাষার আদি নিদর্শন|   
2                                                                                                                                                                                                অষ্টম শতক থেকে বাংলায় রচিত সাহিত্যের বিশাল ভাণ্ডারের মধ্য দিয়ে অষ্টাদশ শতকের শেষে এসে বাংলা ভাষা তার বর্তমান রূপ পরিগ্রহণ করে| বাংলা ভাষার লিপি হল বাংলা লিপি| বাংলাদেশ ও পশ্চিমবঙ্গে প্রচলিত বাংলা ভাষার মধ্যে শব্দগত ও উচ্চারণগত সামান্য পার্থক্য রয়েছে| বাংলার নবজাগরণে ও বাংলার সাংস্কৃতিক বিবিধতাকে এক সূত্রে গ্রন্থনে বাংলা ভাষা ও সাহিত্য সবচেয়ে গুরুত্বপূর্ণ ভূমিকা রেখেছে, এবং বাঙালি জাতীয়তাবাদ তথা বাংলাদেশ গঠনে সবচেয়ে গুরুত্বপূর্ণ ভূমিকা রেখেছে| ১৯৫১-৫২ খ্রিস্টাব্দে পূর্ব বাংলায় সংগঠিত বাংলা ভাষা আন্দোলন এই ভাষার সাথে বাঙালি অস্তিত্বের যোগসূত্র স্থাপন করেছিল|   
3                                                                            ১৯৫২ খ্রিস্টাব্দের ২১শে ফেব্রুয়ারি, ঢাকা বিশ্ববিদ্যালয়ে প্রতিবাদী ছাত্র ও আন্দোলনকারীরা সংখ্যাগরিষ্ঠের মাতৃভাষা বাংলাকে রাষ্ট্রভাষাকরণের দাবীতে নিজেদের জীবন উৎসর্গ করেন| তাঁদের সংগ্রামের স্বীকৃতি স্বরূপ ১৯৯৯ খ্রিস্টাব্দে ইউনেস্কো ২১শে ফেব্রুয়ারি দিনটিকে আন্তর্জাতিক মাতৃভাষা দিবস হিসেবে ঘোষণা করে| ইতিহাস. খ্রিস্টীয় দশম থেকে দ্বাদশ শতাব্দীর মধ্যবর্তী সময়কালে মাগধী প্রাকৃত ও পালির মতো পূর্ব মধ্য ইন্দো-আর্য ভাষাসমূহ থেকে বাংলা ও অন্যান্য পূর্ব ইন্দো-আর্য ভাষাগুলির উদ্ভব ঘটে| এই অঞ্চলে কথ্য ভাষা প্রথম সহস্রাব্দে মাগধী প্রাকৃত বা অর্ধমাগধী ভাষায় বিবর্তিত হয়| খ্রিস্টীয় দশম শতাব্দীর শুরুতে উত্তর ভারতের অন্যান্য প্রাকৃত ভাষার মতোই মাগধী প্রাকৃত থেকে অপভ্রংশ ভাষাগুলির উদ্ভব ঘটে|  

In [ ]:
embeddings_BB[1]

tensor([ 3.3307e-01, -3.3789e-01, -3.7455e-01, -4.0476e-01, -1.8608e-01,
        -2.9365e-01, -1.2444e-01, -1.0123e-01, -6.6478e-01, -2.4775e-01,
         1.4604e-01, -1.4590e-01,  3.3080e-02, -6.8385e-01, -4.1167e-01,
        -4.5451e-01,  1.0046e+00,  6.5717e-01, -6.8576e-02,  7.0888e-01,
         4.8631e-01,  1.2591e+00, -7.2125e-01, -3.7640e-01, -9.0739e-01,
        -7.2926e-01,  3.2534e-01, -5.0305e-01, -2.2186e-01, -1.1155e+00,
        -6.6504e-01, -7.0057e-01,  4.9713e-01, -4.6593e-01, -7.9649e-01,
        -5.2713e-01, -4.3052e-01,  4.8321e-01, -8.6204e-01,  1.6201e-01,
        -4.2847e-01,  4.9575e-01,  3.3640e-01, -4.3777e-01,  7.9408e-01,
        -1.9391e-01, -2.0796e-01,  1.1987e+00, -3.1899e-02, -1.6032e-01,
         4.0763e-01, -2.8572e-01,  1.2522e-01, -5.9809e-01,  8.5339e-01,
        -5.3791e-02,  4.2017e-01, -1.3311e-01, -5.9882e-01, -1.6828e-01,
        -4.4895e-01,  5.2253e-01, -3.4781e-02, -1.6652e-02, -5.2740e-01,
         2.6141e-01, -3.4747e-01, -1.1540e+00,  2.1

#### trial of retrieval

In [ ]:


# Step 2: Import necessary libraries


# Step 3: Load BanglaBERT model and tokenizer
tokenizer = AutoTokenizer.from_pretrained("sagorsarker/bangla-bert-base")
model = AutoModel.from_pretrained("sagorsarker/bangla-bert-base")



/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/491 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/2.24M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/660M [00:00<?, ?B/s]

In [ ]:
# Step 4: Define a function to encode sentences
def encode_sentences(sentences):
    inputs = tokenizer(sentences, return_tensors='pt', padding=True, truncation=True)
    with torch.no_grad():
        outputs = model(**inputs)
    # Mean pooling to get sentence embeddings
    embeddings = outputs.last_hidden_state.mean(dim=1)
    return embeddings.numpy()

In [ ]:
# 1. Define the query
# Note: This could be anything. But since we're working with a nutrition textbook, we'll stick with nutrition-based queries.
query = "সৌরভ"
print(f"Query: {query}")

# 2. Embed the query to the same numerical space as the text examples
# Note: It's important to embed your query with the same model you embedded your examples with.
query_embedding = encode_sentences(query)

# 3. Get similarity scores with the dot product (we'll time this for fun)
from time import perf_counter as timer

# Step 6: Move tensors to CPU and convert to NumPy arrays
query_embedding = torch.tensor(query_embedding).cpu().numpy()
embeddings = torch.tensor(embeddings).cpu().numpy()

start_time = timer()
#dot_scores = util.dot_score(a=query_embedding, b=embeddings)[0]
cosine_scores = cosine_similarity(query_embedding, embeddings)[0]
cosine_scores_tensor = torch.tensor(cosine_scores)
end_time = timer()

print(f"Time take to get scores on {len(embeddings)} embeddings: {end_time-start_time:.5f} seconds.")

# 4. Get the top-k results (we'll keep this to 5)
top_results_dot_product = torch.topk(cosine_scores_tensor, k=5)
top_results_dot_product

Query: সৌরভ
Time take to get scores on 341 embeddings: 0.00656 seconds.


torch.return_types.topk(
values=tensor([0.3862, 0.3219, 0.2653, 0.1968, 0.1947]),
indices=tensor([195,   7,  66, 123,  65]))

In [ ]:
# Define helper function to print wrapped text
#import textwrap

def print_wrapped(text, wrap_length=80):
    wrapped_text = textwrap.fill(text, wrap_length)
    print(wrapped_text)

Now we can loop through the `top_results_dot_product` tuple and match up the scores and indicies and then use those indicies to index on our `pages_and_chunks` variable to get the relevant text chunk.

Sounds like a lot but we can do it!

In [ ]:
print(f"Query: '{query}'\n")
print("Results:")
# Loop through zipped together scores and indicies from torch.topk
for score, idx in zip(top_results_dot_product[0], top_results_dot_product[1]):
    print(f"Score: {score:.4f}")
    # Print relevant sentence chunk (since the scores are in descending order, the most relevant chunk will be first)
    print("Text:")
    print_wrapped(data_and_chunk[idx]["sentence_chunk"])
    # Print the page number too so we can reference the textbook further (and check the results)
    print(f"id: {data_and_chunk[idx]['id']}")
    print(f"title: {data_and_chunk[idx]['title']}")
    print("\n")

Query: 'সৌরভ'

Results:
Score: 0.3862
Text:
তিনি প্রাথমিক শিক্ষা, স্বাস্থ্যব্যবস্থা, খাদ্য, স্বাস্থ্য, পানি ও বিদ্যুত সরবরাহ
নিশ্চিতকল্পে রাষ্ট্রীয় কর্মকাণ্ডের বিস্তৃতি ঘটান| ১৯৭৩ খ্রিস্টাব্দে প্রণীত
বাংলাদেশের প্রথম পঞ্চ বার্ষিক উন্নয়ন পরিকল্পনায় কৃষি, গ্রামীণ অবকাঠামো ও কুটির
শিল্প উন্নয়নে প্রাগ্রাধিকারমূলক সরকারি অর্থ বরাদ্দের নির্দেশ দেয়া হয়|
ধর্মনিরপেক্ষতার প্রতি রাষ্ট্রীয় দায়বদ্ধতা থাকা স্বত্ত্বেও মুজিব ব্যক্তিগত ও
রাষ্ট্রীয় কর্মকাণ্ডের মাধ্যমে ইসলামি অনুশাসনের পথে অগ্রসর হন| তিনি পাকিস্তানি
বাহিনীর সাথে আঁতাতের অভিযোগে ১৯৭২ সালে নিষিদ্ধ ঘোষিত ইসলামিক একাডেমি পুনরায়
চালু করেন| ইসলামিক গোত্রগুলোর জোর দাবির পরিপ্রেক্ষিতে মদ তৈরি ও বিপণন এবং জুয়া
খেলা নিষিদ্ধ করেন|
id: 867
title: শেখ মুজিবুর রহমান


Score: 0.3219
Text:
১৯৫১–৫২ সালে পূর্ব পাকিস্তানে বাঙালি জনগণের প্রবল ভাষা সচেতনতার ফলস্বরূপ বাংলা
ভাষা আন্দোলন নামক একটি ভাষা আন্দোলন গড়ে ওঠে| এই আন্দোলনে পাকিস্তান সরকারের নিকট
বাংলা ভাষার সরকারি স্বীকৃতি দাবি করা হয়| ১৯৫২ খ্রিস্টাব্দে ২১শে ফেব্রুয়ারি
ঢাকা বিশ্ববিদ্যালয় 

### query and context

In [ ]:
import pandas as pd
from google.colab import drive

drive.mount('/content/drive')

save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/query_context_HIL.csv'
df_query_context_HIL = pd.read_csv(save_path)

Mounted at /content/drive


In [ ]:
df_query = df_query_context_HIL['query']

In [ ]:
df_query_context_HIL.head() #for human in the loop output generation, use this variable

query  index  \
0  সারা বিশ্ব কত লোকৈনন্দিন জীবনে বাংলা ব্যবহার করে?      1   
1                          বাংলা ভাষার আদি নিদশন কি?      1   
2                   বাংলাদেশের রাজধানীর জনসংখ্যা কত?      3   
3                    কবে ৬ দফা  আন্দোলনের সূচনা ঘটে?     29   
4  রাষ্ট্রপতি এরশাদ কত খিস্টাব্দ পর্যন্ত দেশ শাসন...     35   

                                             context  
0  ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা...  
1  ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা...  
2  ১৯৫২ খ্রিস্টাব্দের ২১শে ফেব্রুয়ারি, ঢাকা বিশ্...  
3  ১৯৬০-এর দশকের মাঝামাঝি ৬ দফা আন্দোলনের সূচনা ঘ...  
4  রাষ্ট্রপতি এরশাদ ১৯৯০ খ্রিস্টাব্দ পর্যন্ত দেশ ...

In [ ]:
df_query_context_BanglaBert = df_query.copy()
df_query_context_bert_uncased = df_query.copy()

###  BanglaBERT Retrieve

In [ ]:
tokenizer = AutoTokenizer.from_pretrained("sagorsarker/bangla-bert-base")
model = AutoModel.from_pretrained("sagorsarker/bangla-bert-base")


# Step 4: Define a function to encode sentences
def encode_sentences_BB(sentences):
    inputs = tokenizer(sentences, return_tensors='pt', padding=True, truncation=True)
    with torch.no_grad():
        outputs = model(**inputs)
    # Mean pooling to get sentence embeddings
    embeddings = outputs.last_hidden_state.mean(dim=1)
    return embeddings.numpy()

#retrieving
def retrieve_relevant_resources(query: str,
                                embeddings: torch.tensor,

                                n_resources_to_return: int=5,
                                print_time: bool=True):
    """
    Embeds a query with model and returns top k scores and indices from embeddings.
    """


    query_embedding = encode_sentences_BB(query)

    # 3. Get similarity scores with the dot product (we'll time this for fun)
    from time import perf_counter as timer

    # Step 6: Move tensors to CPU and convert to NumPy arrays
    query_embedding = torch.tensor(query_embedding).cpu().numpy()
    embeddings = torch.tensor(embeddings).cpu().numpy()

    start_time = timer()
    #dot_scores = util.dot_score(a=query_embedding, b=embeddings)[0]
    cosine_scores = cosine_similarity(query_embedding, embeddings)[0]
    cosine_scores_tensor = torch.tensor(cosine_scores)
    end_time = timer()



    if print_time:
        print(f"[INFO] Time taken to get scores on {len(embeddings)} embeddings: {end_time-start_time:.5f} seconds.")

    scores, indices = torch.topk(input=cosine_scores_tensor,
                                 k=n_resources_to_return)

    return scores, indices

# Define helper function to print wrapped text
import textwrap

def print_wrapped(text, wrap_length=80):
    wrapped_text = textwrap.fill(text, wrap_length)
    print(wrapped_text)

#seeing retrieval
def print_top_results_and_scores(query: str,
                                 embeddings: torch.tensor,
                                 title_and_chunks: list[dict]=title_and_chunks,
                                 n_resources_to_return: int=5):
    """
    Takes a query, retrieves most relevant resources and prints them out in descending order.

    Note: Requires pages_and_chunks to be formatted in a specific way (see above for reference).
    """

    scores, indices = retrieve_relevant_resources(query=query,
                                                  embeddings=encode_sentences_BB,
                                                  n_resources_to_return=n_resources_to_return)


    print(f"Query: '{query}'\n")
    print("Results:")
    # Loop through zipped together scores and indicies from torch.topk
    for score, idx in zip(scores, indices):
      print(f"Score: {score:.4f}")
      # Print relevant sentence chunk (since the scores are in descending order, the most relevant chunk will be first)
      print("Text:")
      print_wrapped(title_and_chunks[idx]["sentence_chunk"])
      # Print the page number too so we can reference the textbook further (and check the results)
      print(f"id: {title_and_chunks[idx]['id']}")
      print(f"title: {title_and_chunks[idx]['title']}")
      print("\n")

config.json:   0%|          | 0.00/491 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/2.24M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/660M [00:00<?, ?B/s]

In [ ]:

# Define a processing function to generate context for each query
def generate_context_BB(query):
    # Example processing: add a fixed context string
    # Get relevant resources
    scores, indices = retrieve_relevant_resources(query=query,
                                              embeddings=embeddings_BB, n_resources_to_return = 3)
  # Create a list of context items
    context_items = [title_and_chunks[i] for i in indices]
  # Join context items into one dotted paragraph
    context = "- " + "\n- ".join([item["sentence_chunk"] for item in context_items])
    # You can customize the processing logic here
    return context

# Apply the processing function to each query and store the result in a new 'context' column
df_query_context_BanglaBert['context'] = df_query_context_BanglaBert['query'].apply(generate_context_BB)

# Print the updated DataFrame
#print(df_q_context)
df_query_context_BanglaBert.head()

In [ ]:
save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/query_context1.csv'
#df_query_context_BanglaBert.to_csv(save_path, index=False)
df_query_context_BanglaBert = pd.read_csv(save_path)
df_query_context_BanglaBert.head()

###  Bert base multilingual cased Retrieve

In [ ]:
# Import saved file and view

#drive.mount('/content/drive')

embeddings_df_save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/text_chunks_and_embeddings_bert_uncased.csv'
text_chunks_and_embedding_df = pd.read_csv(embeddings_df_save_path)
text_chunks_and_embedding_df.head(1)

In [ ]:
# Rename the unnamed column
text_chunks_and_embedding_df.rename(columns={'Unnamed: 0': 'index'}, inplace=True)
text_chunks_and_embedding_df.describe().round(2)

In [ ]:
def tensor_string_to_list(tensor_string):
    """
    Convert a tensor string to a list of floats.

    Args:
    tensor_string (str): A string representation of a tensor.

    Returns:
    list: A list of floats extracted from the tensor string.
    """
    # Remove the 'tensor([' and '])' parts
    cleaned_string = tensor_string[len("tensor(["):-len("])")]

    # Handle cases with nested brackets
    if cleaned_string.startswith('[') and cleaned_string.endswith(']'):
        cleaned_string = cleaned_string[1:-1]

    # Remove extra spaces and split by comma
    elements = cleaned_string.split(',')

    # Convert to a list of floats
    data_list = [float(element.strip()) for element in elements]

    return data_list


In [ ]:
# Determine the device
device = "cuda" if torch.cuda.is_available() else "cpu"

embeddings_bert_uncased = torch.tensor(text_chunks_and_embedding_df["embedding"], dtype=torch.float32).to(device)
# Convert the list of numpy arrays to a torch tensor and send it to the device

embeddings_bert_uncased.shape

In [ ]:
text_chunks_and_embedding_df.head()

In [ ]:
#retrieving
#Load pre-trained model tokenizer and model
tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased')
model = BertModel.from_pretrained('bert-base-multilingual-cased')

#Function to get sentence embedding
def get_sentence_embedding_bert_uncased(sentence):
    tokens = tokenizer(sentence, return_tensors='pt', padding=True, truncation=True)
    with torch.no_grad():
        outputs = model(**tokens)
    #Get the mean pooling of token embeddings to represent the sentence
    sentence_embedding = outputs.last_hidden_state.mean(dim=1)
    return sentence_embedding

def retrieve_relevant_resources(query: str,
                                embeddings: torch.tensor,

                                n_resources_to_return: int=5,
                                print_time: bool=True):
    """
    Embeds a query with model and returns top k scores and indices from embeddings.
    """


    query_embedding = get_sentence_embedding_bert_uncased(query)

    # 3. Get similarity scores with the dot product (we'll time this for fun)
    from time import perf_counter as timer

    # Step 6: Move tensors to CPU and convert to NumPy arrays
    query_embedding = torch.tensor(query_embedding).cpu().numpy()
    embeddings = torch.tensor(embeddings).cpu().numpy()

    start_time = timer()
    #dot_scores = util.dot_score(a=query_embedding, b=embeddings)[0]
    cosine_scores = cosine_similarity(query_embedding, embeddings)[0]
    cosine_scores_tensor = torch.tensor(cosine_scores)
    end_time = timer()



    if print_time:
        print(f"[INFO] Time taken to get scores on {len(embeddings)} embeddings: {end_time-start_time:.5f} seconds.")

    scores, indices = torch.topk(input=cosine_scores_tensor,
                                 k=n_resources_to_return)

    return scores, indices

# Define helper function to print wrapped text
import textwrap

def print_wrapped(text, wrap_length=80):
    wrapped_text = textwrap.fill(text, wrap_length)
    print(wrapped_text)

#seeing retrieval
def print_top_results_and_scores(query: str,
                                 embeddings: torch.tensor,
                                 title_and_chunks: list[dict]=title_and_chunks,
                                 n_resources_to_return: int=5):
    """
    Takes a query, retrieves most relevant resources and prints them out in descending order.

    Note: Requires pages_and_chunks to be formatted in a specific way (see above for reference).
    """

    scores, indices = retrieve_relevant_resources(query=query,
                                                  embeddings=embeddings,
                                                  n_resources_to_return=n_resources_to_return)


    print(f"Query: '{query}'\n")
    print("Results:")
    # Loop through zipped together scores and indicies from torch.topk
    for score, idx in zip(scores, indices):
      print(f"Score: {score:.4f}")
      # Print relevant sentence chunk (since the scores are in descending order, the most relevant chunk will be first)
      print("Text:")
      print_wrapped(title_and_chunks[idx]["sentence_chunk"])
      # Print the page number too so we can reference the textbook further (and check the results)
      print(f"id: {title_and_chunks[idx]['id']}")
      print(f"title: {title_and_chunks[idx]['title']}")
      print("\n")

In [ ]:
# Define a processing function to generate context for each query
def generate_context_bert_uncased(query):
    # Example processing: add a fixed context string
    # Get relevant resources
    scores, indices = get_sentence_embedding_bert_uncased(query=query,
                                              embeddings=embeddings_bert_uncased, n_resources_to_return = 3)
  # Create a list of context items
    context_items = [title_and_chunks[i] for i in indices]
  # Join context items into one dotted paragraph
    context = "- " + "\n- ".join([item["sentence_chunk"] for item in context_items])
    # You can customize the processing logic here
    return context

# Apply the processing function to each query and store the result in a new 'context' column
df_query_context_bert_uncased['context'] = df_query_context_bert_uncased['query'].apply(generate_context_bert_uncased)

# Print the updated DataFrame
#print(df_q_context)
df_query_context_bert_uncased.head()

In [ ]:
save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/query_context_bert_uncased.csv'
#df_query_context_bert_uncased.to_csv(save_path, index=False)
df_query_context_bert_uncased = pd.read_csv(save_path)
df_query_context_bert_uncased.head()

### Query Context csv to dataframe for answer prediction

In [ ]:
save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/query_context_HIL.csv'
#df_query_context_bert_uncased.to_csv(save_path, index=False)
df_query_context_HIL = pd.read_csv(save_path)
df_query_context_HIL.head()

query  index  \
0  সারা বিশ্ব কত লোকৈনন্দিন জীবনে বাংলা ব্যবহার করে?      1   
1                          বাংলা ভাষার আদি নিদশন কি?      1   
2                   বাংলাদেশের রাজধানীর জনসংখ্যা কত?      3   
3                    কবে ৬ দফা  আন্দোলনের সূচনা ঘটে?     29   
4  রাষ্ট্রপতি এরশাদ কত খিস্টাব্দ পর্যন্ত দেশ শাসন...     35   

                                             context  
0  ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা...  
1  ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা...  
2  ১৯৫২ খ্রিস্টাব্দের ২১শে ফেব্রুয়ারি, ঢাকা বিশ্...  
3  ১৯৬০-এর দশকের মাঝামাঝি ৬ দফা আন্দোলনের সূচনা ঘ...  
4  রাষ্ট্রপতি এরশাদ ১৯৯০ খ্রিস্টাব্দ পর্যন্ত দেশ ...

In [ ]:
save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/query_context_BB.csv'
#df_query_context_BanglaBert.to_csv(save_path, index=False)
df_query_context_BanglaBert = pd.read_csv(save_path)
df_query_context_BanglaBert.head()



query  \
0  সারা বিশ্ব কত লোকৈনন্দিন জীবনে বাংলা ব্যবহার করে?   
1                          বাংলা ভাষার আদি নিদশন কি?   
2           কত লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে?   
3                   বাংলাদেশের রাজধানীর জনসংখ্যা কত?   
4                    কবে ৬ দফা  আন্দোলনের সূচনা ঘটে?   

                                             context  
0  - বাংলাদেশের অবদান ছিল তুলনামূলক ভাবে কম, গুণগ...  
1  - ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাং...  
2  - ভাইয়ের নাম শুনিয়া উনি বড় প্রীত হইল| ভাইয়...  
3  - কিন্তু তারপরও বাংলাদেশে জনসংখ্যার এক বিশাল অ...  
4  - ২০০৫ সালের ২৮ মে, তিনি যুক্তরাজ্যের বৌদ্ধ সো...

In [ ]:
save_path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/query_context_bert_uncased.csv'
#df_query_context_bert_uncased.to_csv(save_path, index=False)
df_query_context_bert_uncased = pd.read_csv(save_path)
df_query_context_bert_uncased.head()

query  \
0  সারা বিশ্ব কত লোকৈনন্দিন জীবনে বাংলা ব্যবহার করে?   
1                          বাংলা ভাষার আদি নিদশন কি?   
2                   বাংলাদেশের রাজধানীর জনসংখ্যা কত?   
3                    কবে ৬ দফা  আন্দোলনের সূচনা ঘটে?   
4  রাষ্ট্রপতি এরশাদ কত খিস্টাব্দ পর্যন্ত দেশ শাসন...   

                                             context  
0  - ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাং...  
1  - পুরাণ ছাড়া সাহিত্যে বা কাব্যে বাংলা বৈষ্ণব ...  
2  - ঢাকা ঢাকা দক্ষিণ এশিয়ার রাষ্ট্র বাংলাদেশের ...  
3  - উনসত্তরের গণঅভ্যুত্থান. বিচারকার্য চলাকালীন ...  
4  - ১৯৮২ সালে জেনারেল এরশাদের ক্ষমতায় আরোহনকে অ...

In [ ]:
def keep_first_three_items(text):
    """
    This function takes a string where items are separated by dashes
    and returns a string containing only the first three items, rejoined by dashes.

    :param text: A string with items separated by dashes
    :return: A string containing only the first three items separated by dashes
    """
    # Split the text by '-' and filter out empty items
    items = [item for item in text.split('-') if item.strip()]

    # Keep only the first three items
    first_three_items = items[:3]

    # Join the first three items back into a single string, separated by dashes
    result = "-" + "-".join(first_three_items)

    return result




In [ ]:
df_query_context_BanglaBert['context'] = df_query_context_BanglaBert['context'].apply(keep_first_three_items)
df_query_context_BanglaBert.head()

query  \
0  সারা বিশ্ব কত লোকৈনন্দিন জীবনে বাংলা ব্যবহার করে?   
1                          বাংলা ভাষার আদি নিদশন কি?   
2           কত লোক দৈনন্দিন জীবনে বাংলা ব্যবহার করে?   
3                   বাংলাদেশের রাজধানীর জনসংখ্যা কত?   
4                    কবে ৬ দফা  আন্দোলনের সূচনা ঘটে?   

                                             context  
0  - বাংলাদেশের অবদান ছিল তুলনামূলক ভাবে কম, গুণগ...  
1  - ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাং...  
2  - ভাইয়ের নাম শুনিয়া উনি বড় প্রীত হইল| ভাইয়...  
3  - কিন্তু তারপরও বাংলাদেশে জনসংখ্যার এক বিশাল অ...  
4  - ২০০৫ সালের ২৮ মে, তিনি যুক্তরাজ্যের বৌদ্ধ সো...

In [ ]:
df_query_context_bert_uncased['context'] = df_query_context_bert_uncased['context'].apply(keep_first_three_items)
df_query_context_bert_uncased.head()

query  \
0  সারা বিশ্ব কত লোকৈনন্দিন জীবনে বাংলা ব্যবহার করে?   
1                          বাংলা ভাষার আদি নিদশন কি?   
2                   বাংলাদেশের রাজধানীর জনসংখ্যা কত?   
3                    কবে ৬ দফা  আন্দোলনের সূচনা ঘটে?   
4  রাষ্ট্রপতি এরশাদ কত খিস্টাব্দ পর্যন্ত দেশ শাসন...   

                                             context  
0  - ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাং...  
1  - পুরাণ ছাড়া সাহিত্যে বা কাব্যে বাংলা বৈষ্ণব ...  
2  - ঢাকা ঢাকা দক্ষিণ এশিয়ার রাষ্ট্র বাংলাদেশের ...  
3  - উনসত্তরের গণঅভ্যুত্থান. বিচারকার্য চলাকালীন ...  
4  - ১৯৮২ সালে জেনারেল এরশাদের ক্ষমতায় আরোহনকে অ...

### LLM Generation

In [ ]:
nf4_config = BitsAndBytesConfig(
   load_in_4bit=True,
   bnb_4bit_quant_type="nf4",
   bnb_4bit_use_double_quant=True,
   bnb_4bit_compute_dtype=torch.bfloat16
)

In [ ]:
model = 'Trelis/Llama-2-7b-chat-hf-sharded-bf16'
#model = 'JamesSpray/llama-2-7b-chat-bnb-4bit-ift-002'
tokenizer = AutoTokenizer.from_pretrained(model)
model = AutoModelForCausalLM.from_pretrained(model, quantization_config=nf4_config)


#model = "meta-llama/Llama-2-7b-chat-hf"

#tokenizer = AutoTokenizer.from_pretrained(model)



tokenizer_config.json:   0%|          | 0.00/719 [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/414 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/658 [00:00<?, ?B/s]

...

pytorch_model-00006-of-00007.bin:   0%|          | 0.00/1.93G [00:00<?, ?B/s]

pytorch_model-00007-of-00007.bin:   0%|          | 0.00/1.66G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/7 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/197 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:540: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuration_utils.py:545: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/configuratio

In [ ]:
pipeline = transformers.pipeline(
    "text-generation", #task
    model=model,
    tokenizer=tokenizer,
    torch_dtype=torch.bfloat16,
    trust_remote_code=True,
    device_map="auto",
    max_length=3000,
    do_sample=True,
    top_k=10,

    num_return_sequences=1,
    eos_token_id=tokenizer.eos_token_id
)



In [ ]:
llm = HuggingFacePipeline(pipeline = pipeline, model_kwargs = {'temperature':0.0001})

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:141: LangChainDeprecationWarning: The class `HuggingFacePipeline` was deprecated in LangChain 0.0.37 and will be removed in 0.3. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFacePipeline`.
  warn_deprecated(


### 0 shot direct

In [ ]:
def gen_0shot(context,query):
  template ="""Based on the following context items, please answer the query in Bangla.
  Context: '''{context}'''
  Query: '{query}'
  Answer:
 """

  prompt = PromptTemplate(template=template, input_variables=["context","query"])

  llm_chain = LLMChain(prompt=prompt, llm=llm)

  prediction1 = llm_chain.run(context=context, query=query)
  return prediction1

In [ ]:
df_query_context_HIL['0shot_direct'] = df_query_context_HIL.apply(lambda x: gen_0shot(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_0shot_direct_t01.csv'
#df_query_context_HIL.to_csv(path, index=False)

In [ ]:
df_query_context_BanglaBert['0shot_direct'] = df_query_context_BanglaBert.apply(lambda x: gen_0shot(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_0shot_direct_t0.0001.csv'
#df_query_context_BanglaBert.to_csv(path, index=False)

In [ ]:
df_query_context_bert_uncased['0shot_direct'] = df_query_context_bert_uncased.apply(lambda x: gen_0shot(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_0shot_direct_t0.0001.csv'
#df_query_context_bert_uncased.to_csv(path, index=False)

### 2 shot

In [ ]:
def gen_2shot(context,query):
  template ="""Based on the following context items, please answer the query. You are given 2 examples below.
  Example 1:
  Context: এ খেলাগুলোয় সাদা রঙের বল ব্যবহার করা হয়|আন্তর্জাতিক ক্রিকেট খেলার নবীনতম সংস্করণ টুয়েন্টি২০। টুয়েন্টি২০ তে  প্রতিটি দল ২০ ওভার করে ব্যাটিং করে।
  Query: আন্তর্জাতিক ক্রিকেট খেলার নবীনতম সংস্করণে প্রতিটি দল কত ওভার করে ব্যাটিং করে?
  Answer: ২০ ওভার

  Example 2:
  Context: ঢাকা দক্ষিণ এশিয়ার রাষ্ট্র বাংলাদেশের রাজধানী । ঢাকা মহানগরী এলাকার জনসংখ্যা প্রায় ১ কোটি ৫০ লক্ষ। জনসংখ্যার বিচারে এটি দক্ষিণ এশিয়ার চতুর্থ বৃহত্তম শহর।
  Query: বাংলাদেশের রাজধানী দক্ষিণ এশিয়ার কততম বৃহত্তম শহর?
  Answer: চতুর্থ

  Context: '''{context}'''
  Query: '{query}'
  Answer:
 """

  prompt = PromptTemplate(template=template, input_variables=["context","query"])

  llm_chain = LLMChain(prompt=prompt, llm=llm)

  prediction1 = llm_chain.run(context=context, query=query)
  return prediction1

In [ ]:
df_query_context_HIL['2shot_direct'] = df_query_context_HIL.apply(lambda x: gen_2shot(x['context'],x['query']), axis=1)
df_query_context_BanglaBert['2shot_direct'] = df_query_context_BanglaBert.apply(lambda x: gen_2shot(x['context'],x['query']), axis=1)
df_query_context_bert_uncased['2shot_direct'] = df_query_context_bert_uncased.apply(lambda x: gen_2shot(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_2shot_direct.csv'
#df_query_context_HIL.to_csv(path, index=False)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_2shot_direct.csv'
#df_query_context_BanglaBert.to_csv(path, index=False)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_2shot_direct.csv'
#df_query_context_bert_uncased.to_csv(path, index=False)

### ReAct

In [ ]:
def gen_ReAct(context,query):
  template ="""Based on the following context items, please answer the query in Bangla.You are given 2 examples below.

  Example 1:
  Context: এ খেলাগুলোয় সাদা রঙের বল ব্যবহার করা হয়|আন্তর্জাতিক ক্রিকেট খেলার নবীনতম সংস্করণ টুয়েন্টি২০। টুয়েন্টি২০ তে  প্রতিটি দল ২০ ওভার করে ব্যাটিং করে।
  Query: আন্তর্জাতিক ক্রিকেট খেলার নবীনতম সংস্করণে প্রতিটি দল কত ওভার করে ব্যাটিং করে?
  Are follow up questions needed here: Yes.
  Follow up:আন্তর্জাতিক ক্রিকেট খেলার নবীনতম সংস্করণ কোনটি?
  Intermediate answer: টুয়েন্টি২০
  Follow up: টুয়েন্টি২০ তে প্রতিটি দল কত ওভার করে ব্যাটিং করে?
  Intermediate answer: টুয়েন্টি২০ তে প্রতিটি দল ২০ ওভার করে ব্যাটিং করে।
  Final answer: ২০ ওভার

  Example 2:
  Context: ঢাকা দক্ষিণ এশিয়ার রাষ্ট্র বাংলাদেশের রাজধানী । ঢাকা মহানগরী এলাকার জনসংখ্যা প্রায় ১ কোটি ৫০ লক্ষ। জনসংখ্যার বিচারে এটি দক্ষিণ এশিয়ার চতুর্থ বৃহত্তম শহর।
  Query: বাংলাদেশের রাজধানী দক্ষিণ এশিয়ার কততম বৃহত্তম শহর?
  Are follow up questions needed here: Yes.
  Follow up:বাংলাদেশের রাজধানী কোনটি?
  Intermediate answer: ঢাকা
  Follow up: ঢাকা দক্ষিণ এশিয়ার কততম বৃহত্তম শহর?
  Intermediate answer: ঢাকা জনসংখ্যার বিচারে দক্ষিণ এশিয়ার চতুর্থ বৃহত্তম শহর.
  Final answer: চতুর্থ


  Context: '''{context}'''
  Query: '{query}'
  Answer:
 """

  prompt = PromptTemplate(template=template, input_variables=["context","query"])

  llm_chain = LLMChain(prompt=prompt, llm=llm)

  prediction1 = llm_chain.run(context=context, query=query)
  return prediction1

In [ ]:
df_query_context_HIL['ReAct'] = df_query_context_HIL.apply(lambda x: gen_ReAct(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_ReAct.csv'
#df_query_context_HIL.to_csv(path, index=False)

In [ ]:
df_query_context_BanglaBert['ReAct'] = df_query_context_BanglaBert.apply(lambda x: gen_ReAct(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_ReAct.csv'
#df_query_context_BanglaBert.to_csv(path, index=False)

In [ ]:
df_query_context_bert_uncased['ReAct'] = df_query_context_bert_uncased.apply(lambda x: gen_ReAct(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_ReAct.csv'
#df_query_context_bert_uncased.to_csv(path, index=False)

### SelfAsk

In [ ]:
def gen_SelfAsk(context,query):
  template ="""Based on the following context items, please answer the query in Bangla.You are given 2 examples below.

  Example 1:
  Context: এ খেলাগুলোয় সাদা রঙের বল ব্যবহার করা হয়|আন্তর্জাতিক ক্রিকেট খেলার নবীনতম সংস্করণ টুয়েন্টি২০। টুয়েন্টি২০ তে  প্রতিটি দল ২০ ওভার করে ব্যাটিং করে।
  Query: আন্তর্জাতিক ক্রিকেট খেলার নবীনতম সংস্করণে প্রতিটি দল কত ওভার করে ব্যাটিং করে?
  Are follow up questions needed here: Yes.
  Follow up:আন্তর্জাতিক ক্রিকেট খেলার নবীনতম সংস্করণ কোনটি?
  {Context}
  Intermediate answer: টুয়েন্টি২০
  Follow up: টুয়েন্টি২০ তে প্রতিটি দল কত ওভার করে ব্যাটিং করে?
  {Context}
  Intermediate answer: টুয়েন্টি২০ তে প্রতিটি দল ২০ ওভার করে ব্যাটিং করে।
  Final answer: ২০ ওভার

  Example 2:
  Context: ঢাকা দক্ষিণ এশিয়ার রাষ্ট্র বাংলাদেশের রাজধানী । ঢাকা মহানগরী এলাকার জনসংখ্যা প্রায় ১ কোটি ৫০ লক্ষ। জনসংখ্যার বিচারে এটি দক্ষিণ এশিয়ার চতুর্থ বৃহত্তম শহর।
  Query: বাংলাদেশের রাজধানী দক্ষিণ এশিয়ার কততম বৃহত্তম শহর?
  Are follow up questions needed here: Yes.
  Follow up:বাংলাদেশের রাজধানী কোনটি?
  {Context}
  Intermediate answer: ঢাকা
  Follow up: ঢাকা দক্ষিণ এশিয়ার কততম বৃহত্তম শহর?
  {Context}
  Intermediate answer: ঢাকা জনসংখ্যার বিচারে দক্ষিণ এশিয়ার চতুর্থ বৃহত্তম শহর.
  Final answer: চতুর্থ


  Context: '''{context}'''
  Query: '{query}'
  Answer:
 """

  prompt = PromptTemplate(template=template, input_variables=["context","query"])

  llm_chain = LLMChain(prompt=prompt, llm=llm)

  prediction1 = llm_chain.run(context=context, query=query)
  return prediction1

In [ ]:
df_query_context_HIL['SelfAsk'] = df_query_context_HIL.apply(lambda x: gen_SelfAsk(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_SelfAsk.csv'
#df_query_context_HIL.to_csv(path, index=False)

In [ ]:
df_query_context_BanglaBert['SelfAsk'] = df_query_context_BanglaBert.apply(lambda x: gen_SelfAsk(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_SelfAsk.csv'
#df_query_context_BanglaBert.to_csv(path, index=False)

In [ ]:
df_query_context_bert_uncased['SelfAsk'] = df_query_context_bert_uncased.apply(lambda x: gen_SelfAsk(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_SelfAsk.csv'
#df_query_context_bert_uncased.to_csv(path, index=False)

### Translative

In [ ]:
def gen_translatory(context,query):
  template ="""Translate the context.
  Translate the quey.
  Answer the query based of the context.
  Translate the answer in Bangla.
  Only provide the Banla answer and nothing else.

  Context: '''{context}'''
  Query: '{query}'
  Answer:
 """

  prompt = PromptTemplate(template=template, input_variables=["context","query"])

  llm_chain = LLMChain(prompt=prompt, llm=llm)

  prediction1 = llm_chain.run(context=context, query=query)
  return prediction1

In [ ]:
df_query_context_HIL['translatory'] = df_query_context_HIL.apply(lambda x: gen_translatory(x['context'],x['query']), axis=1)

#path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_translatory_t0.0001.csv'
#df_query_context_HIL.to_csv(path, index=False)

In [ ]:
df_query_context_BanglaBert['translatory'] = df_query_context_BanglaBert.apply(lambda x: gen_translatory(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_translatory_t0.0001.csv'
#df_query_context_BanglaBert.to_csv(path, index=False)

In [ ]:
df_query_context_bert_uncased['translatory'] = df_query_context_bert_uncased.apply(lambda x: gen_translatory(x['context'],x['query']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_uncased_translatory_t0.0001.csv'
df_query_context_bert_uncased.to_csv(path, index=False)

### TraSe

In [ ]:
def gen_selector(query,context,answer1,answer2):
  template ="""You are given a query and two answers for it.
  Based on the query and context, write from the options [\"Answer1\", \"Answer2\"].
  Answer in the format [Answer: \"Option\"] .
  Query: '{query}'
  Context: '''{context}'''
  Answer1: '''{answer1}'''
  Answer2: '''{answer2}'''

  Selected Option:
 """



  prompt = PromptTemplate(template=template, input_variables=["query","context","answer1", "answer2"])

  llm_chain = LLMChain(prompt=prompt, llm=llm)

  prediction1 = llm_chain.run(query=query,context = context, answer1 = answer1, answer2 = answer2)
  return prediction1

In [ ]:
def extract_answer(paragraph):
    # Find the index where 'Answer: ' starts
    answer_index = paragraph.find("Answer:")

    # If 'Answer: ' is found, extract the text after it
    if answer_index != -1:
        # Add length of 'Answer: ' to get the starting position of the answer
        answer_text = paragraph[answer_index + len("Answer: "):]
        return answer_text.strip()
    else:
        # If 'Answer: ' is not found, return an empty string or a message
        return "No answer found."

#### HIL

In [ ]:
# HIL for t = 0.0001

path1 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_translatory_t0.0001.csv'
df_HIL_translatory = pd.read_csv(path1)

path2 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_0shot_direct_t0.0001.csv'
df_HIL_0shot = pd.read_csv(path2)

path3 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_2shot_direct_t0.0001.csv'
df_HIL_2shot = pd.read_csv(path3)

path4 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_ReAct.csv'
df_HIL_ReAct = pd.read_csv(path4)

path5 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_SelfAsk.csv'
df_HIL_SelfAsk = pd.read_csv(path5)



##### trans+0shot

In [ ]:
df_HIL_Z_T = df_HIL_translatory
df_HIL_Z_T['query'] = df_HIL_translatory['query']
df_HIL_Z_T['context'] = df_HIL_translatory['context']
df_HIL_Z_T['answer1']= df_HIL_translatory['translatory']
df_HIL_Z_T['answer2'] = df_HIL_0shot['0shot_direct']

df_HIL_Z_T['answer1'] = df_HIL_Z_T['answer1'].apply(extract_answer)
df_HIL_Z_T['answer2'] = df_HIL_Z_T['answer2'].apply(extract_answer)

df_HIL_Z_T.head(1)

query  index  \
0  সারা বিশ্ব কত লোকৈনন্দিন জীবনে বাংলা ব্যবহার করে?      1   

                                             context  \
0  ভারতে হিন্দির পরেই সর্বাধিক প্রচলিত ভাষা বাংলা...   

                                        0shot_direct  \
0  Based on the following context items, please a...   

                                         translatory  \
0  Translate the context.\n  Translate the quey.\...   

                                             answer1  \
0  The estimated population of the world as of 20...   

                                             answer2  
0  * ২৬ কোটির অধিক লোকৈন্দিন জীবনে ভাষা ইতিহাস ১২...

In [ ]:
df_HIL_Z_T['selector'] = df_HIL_Z_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_Z&T_t0.0001.csv'
#df_HIL_Z_T.to_csv(path, index=False)


##### trans+2shot

In [ ]:
df_HIL_2_T = df_HIL_translatory
df_HIL_2_T['query'] = df_HIL_translatory['query']
df_HIL_2_T['context'] = df_HIL_translatory['context']
df_HIL_2_T['answer1']= df_HIL_translatory['translatory']
df_HIL_2_T['answer2'] = df_HIL_2shot['2shot_direct']

df_HIL_2_T['answer1'] = df_HIL_2_T['answer1'].apply(extract_answer)
df_HIL_2_T['answer2'] = df_HIL_2_T['answer2'].apply(extract_answer)

df_HIL_2_T['selector'] = df_HIL_2_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_2&T_t0.0001.csv'
#df_HIL_2_T.to_csv(path, index=False)

##### trans+selfask

In [ ]:
df_HIL_S_T = df_HIL_translatory
df_HIL_S_T['query'] = df_HIL_translatory['query']
df_HIL_S_T['context'] = df_HIL_translatory['context']
df_HIL_S_T['answer1']= df_HIL_translatory['translatory']
df_HIL_S_T['answer2'] = df_HIL_SelfAsk['SelfAsk']

df_HIL_S_T['answer1'] = df_HIL_S_T['answer1'].apply(extract_answer)
df_HIL_S_T['answer2'] = df_HIL_S_T['answer2'].apply(extract_answer)

df_HIL_S_T['selector'] = df_HIL_S_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_S&T_t0.0001.csv'
#df_HIL_S_T.to_csv(path, index=False)

##### trans+react

In [ ]:
df_HIL_R_T = df_HIL_translatory
df_HIL_R_T['query'] = df_HIL_translatory['query']
df_HIL_R_T['context'] = df_HIL_translatory['context']
df_HIL_R_T['answer1']= df_HIL_translatory['translatory']
df_HIL_R_T['answer2'] = df_HIL_ReAct['ReAct']

df_HIL_R_T['answer1'] = df_HIL_R_T['answer1'].apply(extract_answer)
df_HIL_R_T['answer2'] = df_HIL_R_T['answer2'].apply(extract_answer)

df_HIL_R_T['selector'] = df_HIL_R_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/HIL_R&T_t0.0001.csv'
#df_HIL_R_T.to_csv(path, index=False)

#### BanglaBERT

In [ ]:
path1 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_translatory_t0.0001.csv'
df_BB_translatory = pd.read_csv(path1)

path2 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_0shot_direct_t0.0001.csv'
df_BB_0shot = pd.read_csv(path2)

path3 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_2shot_direct_t0.0001.csv'
df_BB_2shot = pd.read_csv(path3)

path4 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_ReAct.csv'
df_BB_ReAct = pd.read_csv(path4)

path5 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_SelfAsk.csv'
df_BB_SelfAsk = pd.read_csv(path5)



##### trans+0shot

In [ ]:
df_BB_Z_T = df_BB_translatory
df_BB_Z_T['query'] = df_BB_translatory['query']
df_BB_Z_T['context'] = df_BB_translatory['context']
df_BB_Z_T['answer1']= df_BB_translatory['translatory']
df_BB_Z_T['answer2'] = df_BB_0shot['0shot_direct']

df_BB_Z_T['answer1'] = df_BB_Z_T['answer1'].apply(extract_answer)
df_BB_Z_T['answer2'] = df_BB_Z_T['answer2'].apply(extract_answer)

df_BB_Z_T['selector'] = df_BB_Z_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_Z&T_t0.0001.csv'
#df_BB_Z_T.to_csv(path, index=False)

##### trans+2shot

In [ ]:
df_BB_2_T = df_BB_translatory
df_BB_2_T['query'] = df_BB_translatory['query']
df_BB_2_T['context'] = df_BB_translatory['context']
df_BB_2_T['answer1']= df_BB_translatory['translatory']
df_BB_2_T['answer2'] = df_BB_2shot['2shot_direct']

df_BB_2_T['answer1'] = df_BB_2_T['answer1'].apply(extract_answer)
df_BB_2_T['answer2'] = df_BB_2_T['answer2'].apply(extract_answer)

df_BB_2_T['selector'] = df_BB_2_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_2&T_t0.0001.csv'
#df_BB_2_T.to_csv(path, index=False)

##### trans+selfask

In [ ]:
df_BB_S_T = df_BB_translatory
df_BB_S_T['query'] = df_BB_translatory['query']
df_BB_S_T['context'] = df_BB_translatory['context']
df_BB_S_T['answer1']= df_BB_translatory['translatory']
df_BB_S_T['answer2'] = df_BB_SelfAsk['SelfAsk']

df_BB_S_T['answer1'] = df_BB_S_T['answer1'].apply(extract_answer)
df_BB_S_T['answer2'] = df_BB_S_T['answer2'].apply(extract_answer)

df_BB_S_T['selector'] = df_BB_S_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_S&T_t0.0001.csv'
#df_BB_S_T.to_csv(path, index=False)

In [ ]:
# trans+react
df_BB_R_T = df_BB_translatory
df_BB_R_T['query'] = df_BB_translatory['query']
df_BB_R_T['context'] = df_BB_translatory['context']
df_BB_R_T['answer1']= df_BB_translatory['translatory']
df_BB_R_T['answer2'] = df_BB_ReAct['ReAct']

df_BB_R_T['answer1'] = df_BB_R_T['answer1'].apply(extract_answer)
df_BB_R_T['answer2'] = df_BB_R_T['answer2'].apply(extract_answer)

df_BB_R_T['selector'] = df_BB_R_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/BB_R&T_t0.0001.csv'
#df_BB_R_T.to_csv(path, index=False)

####bert base

In [ ]:
path1 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_uncased_translatory_t0.0001.csv'
df_bert_translatory = pd.read_csv(path1)

path2 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_uncased_0shot_direct_t0.0001.csv'
df_bert_0shot = pd.read_csv(path2)

path3 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_uncased_2shot_direct_t0.0001.csv'
df_bert_2shot = pd.read_csv(path3)

path4 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_uncased_ReAct.csv'
df_bert_ReAct = pd.read_csv(path4)

path5 = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_uncased_SelfAsk.csv'
df_bert_SelfAsk = pd.read_csv(path5)

In [ ]:
df_bert_Z_T = df_bert_translatory
df_bert_Z_T['query'] = df_bert_translatory['query']
df_bert_Z_T['context'] = df_bert_translatory['context']
df_bert_Z_T['answer1']= df_bert_translatory['translatory']
df_bert_Z_T['answer2'] = df_bert_translatory['0shot_direct']

df_bert_Z_T['answer1'] = df_bert_Z_T['answer1'].apply(extract_answer)
df_bert_Z_T['answer2'] = df_bert_Z_T['answer2'].apply(extract_answer)

df_bert_Z_T['selector'] = df_bert_Z_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_Z&T_t0.0001.csv'
#df_bert_Z_T.to_csv(path, index=False)

In [ ]:
#trans+2shot
df_bert_2_T = df_bert_translatory
df_bert_2_T['query'] = df_bert_translatory['query']
df_bert_2_T['context'] = df_bert_translatory['context']
df_bert_2_T['answer1']= df_bert_translatory['translatory']
df_bert_2_T['answer2'] = df_bert_2shot['2shot_direct']

df_bert_2_T['answer1'] = df_bert_2_T['answer1'].apply(extract_answer)
df_bert_2_T['answer2'] = df_bert_2_T['answer2'].apply(extract_answer)

df_bert_2_T['selector'] = df_bert_2_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_2&T_t0.0001.csv'
#df_bert_2_T.to_csv(path, index=False)

In [ ]:
#trans+selfask
df_bert_S_T = df_bert_translatory
df_bert_S_T['query'] = df_bert_translatory['query']
df_bert_S_T['context'] = df_bert_translatory['context']
df_bert_S_T['answer1']= df_bert_translatory['translatory']
df_bert_S_T['answer2'] = df_bert_SelfAsk['SelfAsk']

df_bert_S_T['answer1'] = df_bert_S_T['answer1'].apply(extract_answer)
df_bert_S_T['answer2'] = df_bert_S_T['answer2'].apply(extract_answer)

df_bert_S_T['selector'] = df_bert_S_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_S&T_t0.0001.csv'
#df_bert_S_T.to_csv(path, index=False)

In [ ]:
# trans+react
df_bert_R_T = df_bert_translatory
df_bert_R_T['query'] = df_bert_translatory['query']
df_bert_R_T['context'] = df_bert_translatory['context']
df_bert_R_T['answer1']= df_bert_translatory['translatory']
df_bert_R_T['answer2'] = df_bert_ReAct['ReAct']

df_bert_R_T['answer1'] = df_bert_R_T['answer1'].apply(extract_answer)
df_bert_R_T['answer2'] = df_bert_R_T['answer2'].apply(extract_answer)

df_bert_R_T['selector'] = df_bert_R_T.apply(lambda x: gen_selector(x['query'],x['context'],x['answer1'],x['answer2']), axis=1)

path = '/content/drive/MyDrive/data/Bangla_RAG_wiki/bert_R&T_t0.0001.csv'
#df_bert_R_T.to_csv(path, index=False)